In [1]:
import numpy as np
import random
from PIL import Image
from collections import deque
from keras.models import Sequential
from keras import initializers
from keras.layers import Dense, Conv2D, Dropout, Flatten
from keras.optimizers import Adam, Nadam, Adamax
sizes = (80,80,1)

class Agent:
    def __init__(self, state_size, action_size):
        self.state_size = state_size
        self.action_size = action_size
        self.memory = deque(maxlen=50000)
        self.gamma = 0.999   # discount rate
        self.epsilon = 1.0  # exploration rate
        self.epsilon_min = 0.00  # exploration will not decay futher
        self.epsilon_decay = 0.000995
        self.learning_rate = 0.0001
        self.model = self._build_model()
        self.weight_backup = 'model_weights.h5'

    def _build_model(self):
        model = Sequential()
        model.add(Conv2D(32, kernel_size=8, subsample=(4, 4), activation='relu', kernel_initializer='random_uniform', bias_initializer='zeros', padding='same', input_shape= sizes))#80*80*4
        model.add(Conv2D(64, kernel_size=4, subsample=(2, 2), activation='relu', padding='same'))
        model.add(Conv2D(64, kernel_size=3, subsample=(1, 1), activation='relu', padding='same'))
        model.add(Flatten())
        model.add(Dense(512, activation='relu'))
        model.add(Dense(self.action_size))
        model.compile(loss='mse', optimizer=Adam(lr=self.learning_rate))
        return model

    '''
    def _build_model(self):
        # Neural Net for Deep-Q learning Model
        model = Sequential()
        model.add(Dense(20, input_dim=self.state_size, activation='elu'))
        #model.add(Dropout(0.1))
        model.add(Dense(20, activation='elu'))
        #model.add(Dropout(0.2))
        model.add(Dense(self.action_size, activation='linear'))
        model.compile(loss='mse', optimizer=Nadam(lr=self.learning_rate))
        return model
    '''
    
    def save_model(self):
            self.model.save(self.weight_backup)

    def act(self, state):
        if np.random.rand() <= self.epsilon:
            return random.randrange(self.action_size)
        act_values = self.model.predict(state)
        return np.argmax(act_values[0])

    def remember(self, state, action, reward, new_state, done):
        self.memory.append([state, action, reward, new_state, done])
    
        '''
        if reward == 0.0:
            pass
        else:
            for m in self.memory[-5:-1]:
                if self.memory[-1][2] == 1.0:
                    m[2] = 1.0
                    pass
                elif self.memory[-1][2] == -1.0:
                    m[2] = -1.0
                    pass
         '''           

    def memory_replay(self, batch_size):
        if len(self.memory) < batch_size:
            return
        Sample = random.sample(self.memory, batch_size)
        winsample = [s for s in self.memory if s[2]== 1.0]
        #print(winsample)
        tuple(winsample)
        if len(winsample) > batch_size:
            Samplewin = random.sample(winsample, batch_size)
            Sample += Samplewin
        else:  
            Sample += winsample
        for state, action, reward, new_state, done in Sample:
            target = reward
            if not done:
                target = reward + self.gamma * np.amax(self.model.predict(new_state))
            target_f = self.model.predict(state)
            print(action, reward, target_f)
            target_f[0] = target
            self.model.fit(state, target_f, epochs=1, verbose=0)
        if self.epsilon > self.epsilon_min:
            self.epsilon -= self.epsilon_decay
    '''        
    def RGBprocess(new_state):
        processed_observation = Image.fromarray(new_state, 'RGB')
        processed_observation = processed_observation.convert('L')
        processed_observation = processed_observation.resize((80, 80))
        processed_observation = np.array(processed_observation)
        processed_observation = processed_observation.reshape(1, processed_observation.shape[0], processed_observation.shape[1], 1) #1x80x80x1
        return processed_observation
        #stack4.append(processed_observation)
        #if len(stack4) == 4:
            #stack_of_observation = np.stack((processed_observation, processed_observation, processed_observation, processed_observation), axis=2)
            #stack_of_observation = stack_of_observation.reshape(stack_of_observation.shape[0], stack_of_observation.shape[1], stack_of_observation.shape[3], stack_of_observation.shape[2])
            #print(stack_of_observation.shape)
    '''

Using TensorFlow backend.


In [2]:
import sys
import gym
from gym import wrappers


def RGBprocess(raw_img):
        processed_observation = Image.fromarray(raw_img, 'RGB')
        processed_observation = processed_observation.convert('L')
        processed_observation = processed_observation.resize((80, 80))
        processed_observation = np.array(processed_observation)
        processed_observation = processed_observation.reshape(1, processed_observation.shape[0], processed_observation.shape[1], 1) #1x80x80x1
        return processed_observation
'''
def RGBprocess(raw_img):
    I = raw_img[35:195] # crop
    I = I[::2,::2,0] # downsample by factor of 2
    I[I == 144] = 0 # erase background (background type 1)
    I[I == 109] = 0 # erase background (background type 2)
    I[I != 0] = 1 # everything else (paddles, ball) just set to 1
    processed_observation = I
    return processed_observation.astype(np.float).ravel()
'''

batch_size = 16
#episodes = sys.argv[1] if len(sys.argv) > 1 else 5000
#env_name = sys.argv[2] if len(sys.argv) > 2 else "Pong-v0"

episodes = 2000
env_name = "Pong-v0"
D = 80*80
prev_x = None

env = gym.make(env_name)

env = wrappers.Monitor(env, env_name, force=True)

agent = Agent(env.observation_space.shape, env.action_space.n)

for i_episodes in range(episodes):
    state = env.reset()
    totalreward = 0
    num_actions = 0
    short_mem = []
    done = False
    state = RGBprocess(state)
    while not done:
        #env.render()
        action = agent.act(state)
        new_state, reward, done, info = env.step(action)
        new_state = RGBprocess(new_state)
        new_state_dif = new_state - prev_x if prev_x is not None else new_state
        prev_x = new_state
        if reward == 0:
            num_actions += 1
            short_mem.append([state, action, reward, new_state_dif, done])
        else:
            num_actions += 1
            short_mem.append([state, action, reward, new_state_dif, done])
            if reward == -1.0:
                for m in short_mem:
                    m[2] = -1.0
                    agent.remember(m[0], m[1], m[2], m[3], m[4])
                num_actions = 0
            elif reward == 1.0:
                for m in short_mem:
                    m[2] = 1.0
                    agent.remember(m[0], m[1], m[2], m[3], m[4])
            short_mem = []
        state = new_state_dif
        totalreward += reward
    agent.memory_replay(batch_size)
    if done:
        print("{} episode, score = {} ".format(i_episodes + 1, totalreward))
        agent.save_model()

env.close()
gym.upload(env_name, api_key='sk_WRCITkqmTJKYB9hvBk5tPA')

[2017-08-18 23:49:25,119] Making new env: Pong-v0
[2017-08-18 23:49:25,303] Clearing 10 monitor files from previous run (because force=True was provided)
/home/z0m6ie/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:26: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(32, kernel_size=8, activation="relu", kernel_initializer="random_uniform", bias_initializer="zeros", padding="same", input_shape=(80, 80, 1..., strides=(4, 4))`
/home/z0m6ie/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:27: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(64, kernel_size=4, activation="relu", padding="same", strides=(2, 2))`
/home/z0m6ie/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:28: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(64, kernel_size=3, activation="relu", padding="same", strides=(1, 1))`
[2017-08-18 23:49:25,392] Starting new video recorder writing to /home/z0m6ie/Documents/GitHub/Machine_Learning

3 -1.0 [[ 0.  0.  0.  0.  0.  0.]]
4 -1.0 [[-0.08839783 -0.47241491 -0.3273336  -0.67523998 -0.42223743 -0.5199371 ]]
5 -1.0 [[ 0.1737984  -0.30694389  0.25200814 -0.77586997  0.18413971  0.47429678]]
0 -1.0 [[-0.19981259 -0.32363302 -0.53578949 -0.34131622  0.03230666 -0.76902896]]
4 -1.0 [[-0.37428525 -0.43921635 -0.41668049 -0.07231731 -0.54251075 -0.24825315]]
3 -1.0 [[-0.73171502 -0.50544751 -1.81119478 -1.31069183 -1.14423895 -0.36188713]]
3 1.0 [[-0.88078213 -0.94261181 -0.78057927 -0.26854599 -0.89824826 -0.45680907]]
4 -1.0 [[-1.36927164 -0.61509687 -1.53874969 -1.50689805 -1.64085889 -0.53035456]]
5 -1.0 [[-2.3840065  -1.85345244 -1.54274273 -1.81127203 -2.05537748 -1.63196433]]
4 -1.0 [[-0.76861489 -1.247177   -0.65036583 -0.67881292 -0.86954802 -0.87026447]]
4 -1.0 [[-1.04867291 -0.88129568 -0.8208856  -0.09451941  0.10916642 -0.39498642]]
3 -1.0 [[-0.88039458 -1.07052243 -0.6922707   0.0846779  -0.35532117  0.212982  ]]
2 -1.0 [[-1.49541628 -1.63050675 -1.21141553 -1.09388

[2017-08-18 23:49:28,624] Starting new video recorder writing to /home/z0m6ie/Documents/GitHub/Machine_Learning_Projects/deep-Q-learning/Test/Pong-v0/openaigym.video.0.3898.video000001.mp4


2 -1.0 [[-1.24509966 -0.49106133 -0.79578376 -0.97246987 -1.09921753 -1.38384366]]
0 -1.0 [[-1.45275319 -1.07200944 -0.34337339 -1.39253783 -0.95871437 -1.8346566 ]]
5 -1.0 [[-0.18607579  0.36803725  0.34104702  0.72408116  0.48343939 -0.07416902]]
3 -1.0 [[-2.18569589 -3.04814982 -1.02967143 -2.31755924 -1.23543108 -3.53959346]]
1 -1.0 [[ 1.49370754  0.54909152  1.23420036  1.51437902  1.79919004  0.67562336]]
5 -1.0 [[ 2.97753692  2.414572    2.38126969  3.35607934  3.17916775  2.60449338]]
2 -1.0 [[-0.15939435 -0.43514261 -0.1943178   0.43040174 -0.04891149 -0.33827007]]
0 -1.0 [[ 0.03108028 -0.58611465 -0.39058903 -0.8354162  -0.65429991 -0.56874901]]
2 -1.0 [[ 1.68625176  1.75225365  1.83289599  2.70531344  2.54210663  2.37363887]]
3 -1.0 [[-0.8552922  -0.91428936 -1.41563308 -0.99215513 -1.56986547 -0.78717273]]
1 -1.0 [[ 0.91413641  1.02657723  1.13565218  0.55293459  1.16035283  1.15079927]]
4 1.0 [[ 2.69275403  2.55832434  2.24359965  3.2086339   3.27501273  3.3887496 ]]
5 -1.

5 -1.0 [[ 3.95125937  3.55894136  3.75147557  3.64419985  3.29316092  3.63146663]]
4 -1.0 [[-0.15474801  0.07451809 -0.57695699  0.13246529  0.12003575  0.64885098]]
1 -1.0 [[ 1.92904627  1.79595685  1.75516033  1.35634673  2.0302217   1.53804493]]
3 -1.0 [[ 2.25828266  1.35170913  2.05864835  1.67947924  2.2310555   2.18147683]]
2 -1.0 [[ 3.51615524  3.54780149  3.47048473  3.29631853  3.8239162   3.41479254]]
5 -1.0 [[ 1.21833098  1.08349252  1.19048572  1.01245165  1.02421737  1.09568763]]
4 -1.0 [[ 3.83052158  3.51756191  3.41018319  3.09963036  3.56939125  3.49720001]]
4 -1.0 [[ 1.33337963  1.85096157  1.63979805  1.50741565  1.06307626  0.78535563]]
5 -1.0 [[ 3.30649757  2.91416621  2.95123696  2.7674377   2.35278082  2.9948802 ]]
3 -1.0 [[ 3.01482153  3.03377032  3.34605455  2.6676116   2.4779284   2.87786317]]
3 -1.0 [[ 1.46495891  1.56330824  1.12749493  1.63193965  1.72548747  1.20879328]]
1 1.0 [[ 4.24283552  4.30817747  4.11097956  4.11668539  4.19913054  4.18047142]]
5 1.0

...

3 -1.0 [[ 128.41737366  127.28900146  128.2368927   127.86708069  128.11499023
   127.60269165]]
1 -1.0 [[ 125.88838959  125.92266846  125.74041748  126.43149567  126.93106079
   125.92087555]]
5 -1.0 [[ 127.42031097  127.09125519  127.4773407   127.26222229  127.71333313
   127.09513855]]
2 -1.0 [[ 123.79180145  123.79043579  124.21058655  123.70063019  123.95469666
   123.5641861 ]]
4 -1.0 [[ 121.54600525  121.41977692  120.99718475  121.72786713  122.24406433
   121.51152802]]
1 -1.0 [[ 126.90940094  127.15885162  127.27140045  127.11134338  127.64291382
   127.22837067]]
2 -1.0 [[ 122.5509491   122.25495148  122.15318298  122.21600342  122.41343689
   122.42773438]]
0 -1.0 [[ 123.24152374  123.68831635  123.26271057  123.48336029  123.77677917
   123.85137177]]
2 -1.0 [[ 121.26338959  121.22598267  121.07482147  121.16048431  121.42783356
   121.59529877]]
2 -1.0 [[ 119.8212738   119.29473114  120.3115387   118.58087921  118.49681854
   119.63974762]]
1 -1.0 [[ 124.5157547   124.97

3 1.0 [[ 138.91296387  138.89234924  138.2624054   139.13490295  138.81156921
   138.93412781]]
3 1.0 [[ 140.58787537  140.04649353  139.67756653  140.61680603  140.16740417
   140.04867554]]
1 1.0 [[ 134.40245056  135.12141418  134.43490601  135.21177673  134.72906494
   134.57434082]]
2 1.0 [[ 149.39501953  150.35394287  149.92373657  149.95425415  149.98576355
   149.81013489]]
5 1.0 [[ 141.50024414  141.64245605  141.20574951  141.63261414  141.73033142
   141.78593445]]
1 1.0 [[ 136.36030579  136.80145264  136.50523376  136.47129822  136.40867615
   136.32777405]]
3 1.0 [[ 142.41235352  141.89231873  142.31692505  142.49606323  142.31671143
   142.06199646]]
1995 episode, score = -21.0 
2 -1.0 [[ 135.81079102  135.69009399  135.93930054  135.47276306  135.56535339
   135.43637085]]
1 -1.0 [[ 136.98455811  136.96372986  136.99479675  136.72514343  136.72042847
   136.93928528]]
1 -1.0 [[ 136.75637817  136.66685486  136.63070679  136.42962646  136.61001587
   136.43084717]]
0 -1.0 [

4 -1.0 [[ 151.46591187  151.22341919  151.57240295  151.71603394  151.54759216
   151.35406494]]
3 1.0 [[ 156.45158386  156.92401123  156.75672913  157.15579224  156.68095398
   157.38763428]]
0 1.0 [[ 149.0965271   149.445755    149.5057373   149.53179932  149.29322815
   149.5050354 ]]
1 1.0 [[ 158.27441406  158.71681213  159.05314636  158.64892578  158.93063354
   158.89982605]]
4 1.0 [[ 158.27252197  157.76950073  157.81884766  158.25401306  158.41082764
   157.83106995]]
5 1.0 [[ 156.99617004  156.98678589  156.98692322  157.53294373  157.31825256
   157.15583801]]
1 1.0 [[ 160.31851196  160.31741333  160.08992004  160.14213562  160.31027222
   160.35757446]]
3 1.0 [[ 151.11779785  150.72224426  150.8256073   151.12567139  151.00144958
   150.80747986]]
3 1.0 [[ 153.37719727  152.74346924  153.05212402  152.99508667  152.74002075
   152.71516418]]
5 1.0 [[ 155.5433197   155.20022583  154.86737061  155.48225403  155.28793335
   155.17611694]]
4 1.0 [[ 155.67329407  155.58218384  15

[2017-08-19 02:14:28,506] Finished writing results. You can upload them to the scoreboard via gym.upload('/home/z0m6ie/Documents/GitHub/Machine_Learning_Projects/deep-Q-learning/Test/Pong-v0')
[2017-08-19 02:14:28,510] [Pong-v0] Uploading 2000 episodes of training data


APIConnectionError: Unexpected error communicating with OpenAI Gym (while calling post https://gym-api.openai.com/v1/files). If this problem persists, let us
know at gym@openai.com.

(Network error: ReadTimeout: HTTPSConnectionPool(host='gym-api.openai.com', port=443): Read timed out. (read timeout=200))

In [3]:
gym.upload(env_name, api_key='sk_WRCITkqmTJKYB9hvBk5tPA')

[2017-08-19 07:48:30,080] [Pong-v0] Uploading 2000 episodes of training data


APIConnectionError: Unexpected error communicating with OpenAI Gym (while calling post https://gym-api.openai.com/v1/files). If this problem persists, let us
know at gym@openai.com.

(Network error: ConnectionError: HTTPSConnectionPool(host='gym-api.openai.com', port=443): Max retries exceeded with url: /v1/files (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x7f059f68c080>: Failed to establish a new connection: [Errno 111] Connection refused',)))

In [ ]:
state.shape

In [ ]:
reward

In [ ]:
test = agent.model.predict(state)

In [ ]:
test[0]

In [ ]:
env.reset()
env.close()

In [ ]:
len(agent.memory)

In [ ]:
processed_observation = Image.fromarray(state, 'RGB')
processed_observation = processed_observation.convert('L')
processed_observation = processed_observation.resize((80, 80))
processed_observation = np.array(processed_observation)
processed_observation = processed_observation.reshape(processed_observation.shape[0], processed_observation.shape[1], 1)

In [ ]:
new_state

In [ ]:
def RGBprocess(new_state):
        processed_observation = Image.fromarray(new_state, 'RGB')
        processed_observation = processed_observation.convert('L')
        processed_observation = processed_observation.resize((80, 80))
        processed_observation = np.array(processed_observation)
        processed_observation = processed_observation.reshape(processed_observation.shape[0], processed_observation.shape[1], 1) #1x80x80x1
        return processed_observation

In [ ]:
new_state_dif = new_state_dif.reshape(new_state_dif.shape[1], new_state_dif.shape[2])
img = Image.fromarray(new_state_dif, 'L')

In [ ]:
img.show()

In [ ]:
thing = [1,2,3,4,5,6]
for x in thing[-2:]:
    print(x)